# &nbsp; 0. Colab init

In [92]:
%%capture
!pip install geopandas==0.10.2
!pip install mapclassify==2.4.3
!pip install selenium==4.2.0
!pip install pygeos==0.10.2
!pip install -U folium

In [93]:
from folium import GeoJson, GeoJsonTooltip, Map, Marker, Icon, PolyLine, FeatureGroup
from folium.plugins import MarkerCluster
from shapely.geometry import LineString
from geopy.geocoders import Nominatim
from folium.map import LayerControl
import matplotlib.pyplot as plt
from google.colab import drive
import plotly.express as px
from tqdm.auto import tqdm
import geopandas as gpd
import seaborn as sns
import pandas as pd
import numpy as np
import sys, os, re
import folium
import json

drive.mount('/content/drive')

folder_directory = "/content/drive/MyDrive/_____SHARED/Geospatial"
sys.path.append(folder_directory)
os.chdir(folder_directory)

import utils
import styles
tiles = 'Stamen Terrain'

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


# &nbsp; 1. OpenStreetMap and OverPass API Turbo

First we will extract all the nodes marked as 'alpine_hut' from OSM for having a available more data about Veneto, Trento, Bolzano.

Thanks to Overpass api we could query from geocodeArea, this is the reason why we manually download them as GeoJson.

```
@https://overpass-turbo.eu/

[out:json][timeout:25];
{{geocodeArea:Veneto}}->.searchArea;
(
  node["tourism"="alpine_hut"](area.searchArea);
  way["tourism"="alpine_hut"](area.searchArea);
);

out body;
```

In [94]:
osm_rifugi = pd.concat([
  gpd.read_file('data/alpine_huts/bolzano_rifugi_osm.geojson'),
  gpd.read_file('data/alpine_huts/trento_rifugi_osm.geojson'),
  gpd.read_file('data/alpine_huts/veneto_rifugi_osm.geojson')                        
])

# load previusly prepared gdf
dolomiti_df = gpd.read_file('data/geo_dolomiti/dolomiti_geo.shp')
dolomiti_df.loc[2, ["name"]] = "Sistema 3 - Pale di San Martino"

# create the folium geojson for next rendering
dolomiti_geo = GeoJson(
    data = dolomiti_df,
    style_function = styles.style_dolomiti,
    tooltip = GeoJsonTooltip(fields=['name', 'url_info', 'area'])
  )

# load italian geospatial data
dolomiti_regions, dolomiti_provincies, dolomiti_municipalities = utils.load_italian_north_east_area()

In [101]:
dolomiti_regions.crs

<Geographic 2D CRS: EPSG:4326>
Name: WGS 84
Axis Info [ellipsoidal]:
- Lat[north]: Geodetic latitude (degree)
- Lon[east]: Geodetic longitude (degree)
Area of Use:
- name: World.
- bounds: (-180.0, -90.0, 180.0, 90.0)
Datum: World Geodetic System 1984 ensemble
- Ellipsoid: WGS 84
- Prime Meridian: Greenwich

In [99]:
dolomiti_regions.to_file('data/italy/italy_nord_ovest.shp')

In [95]:
# Some preprocessing
osm_rifugi.replace({np.nan: None}, inplace=True)
osm_rifugi.dropna(subset=['name'], inplace=True)

selection = ['addr:city', 
             'name',
             'ele', 
             'operator', 
             'opening_hours',
             'capacity', 
             'contact:email', 
             'contact:mobile', 
             'website',
             'geometry',
            ]

print(osm_rifugi.columns)
osm_rifugi = osm_rifugi.loc[:, selection]

# removing 'malga'
osm_rifugi = osm_rifugi.loc[osm_rifugi.name.apply(
    lambda x: ('hütte' in x.lower() or 'rifugio' in x.lower()) and 'malga' not in x.lower()
  )]

# be sure that all the hut are marked as points and not multipolygon
osm_rifugi.geometry = osm_rifugi.geometry.apply(utils.from_poly_to_point)
osm_rifugi.reset_index(drop=True, inplace=True)

# set proper type of 'ele' which stand for the elevation on the sea level
osm_rifugi.ele = osm_rifugi.ele.str.replace('m', '')
osm_rifugi.ele.fillna(0, inplace=True)
osm_rifugi.ele = osm_rifugi.ele.astype(float)

# set the province
assert dolomiti_provincies.crs == osm_rifugi.crs
osm_rifugi['DEN_PROV'] = osm_rifugi.geometry.apply(lambda x: utils.element_within_area(x, dolomiti_provincies, 'DEN_PROV'))
osm_rifugi = osm_rifugi[~osm_rifugi.DEN_PROV.isna()]

unique_provice_dolomities = osm_rifugi.DEN_PROV.unique().tolist()

if not 'osm_rifugi_processed.shp' is os.listdir('data/alpine_huts'):
  osm_rifugi.to_file('data//alpine_huts/osm_rifugi_processed.shp')

Index(['id', '@id', 'access', 'addr:city', 'addr:city:de', 'addr:city:it',
       'addr:city:lld', 'addr:country', 'addr:hamlet', 'addr:hamlet:de',
       ...
       'tourism_2', 'wikimedia_commons', 'addr:locality', 'disused:building',
       'int_name', 'lunch', 'name:en', 'opening_hours:it', 'source:name',
       'state'],
      dtype='object', length=167)


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:42: UserWarning: Column names longer than 10 characters will be truncated when saved to ESRI Shapefile.


## &nbsp; 1.1 Alpine huts divided by regions
First explorations to understand where the majority of the huts are located.


In [ ]:
#  https://stackoverflow.com/questions/37466683/create-a-legend-on-a-folium-map

osm_hut_map = utils.get_new_map(title='Hut divided by region of provenience', tiles=tiles)
colors = ['gray', 'lightgreen', 'green', 'orange', 'darkred','black']

feature_layers = {
    group: FeatureGroup(name=f"<span style='color:{styles.c_colors[idx]}'>Hut in {group}</span>") 
    for idx, group in enumerate(unique_provice_dolomities)
  }

marker_clusters_ops = {
    'zoomToBoundsOnClick': False, 'maxClusterRadius': 110, 'spiderfyOnMaxZoom': 2, 'disableClusteringAtZoom': 10
  }

marker_clusters = {
    group: MarkerCluster(
        options = marker_clusters_ops,
        name = f"<span style='color:{styles.c_colors[idx]}'>Hut in {group}</span>"
      ) 
    for idx, group in enumerate(unique_provice_dolomities)
  }

feature_layers['dolomiti_area'] =  FeatureGroup(name='Area Dolomiti')
dolomiti_geo.add_to(feature_layers['dolomiti_area'])

# add huts to the map
for idx, row in osm_rifugi.iterrows():
  marker_group = row.DEN_PROV
  marker = Marker(
      location = [i[0] for i in reversed(row.geometry.xy)],
      popup = utils.get_info_from_row(row), 
      tooltip = utils.get_info_from_row(row),
      icon = Icon(color = styles.c_colors[unique_provice_dolomities.index(row.DEN_PROV)])
  )
  marker.add_to(marker_clusters[marker_group])

for k,v in marker_clusters.items():
  marker_clusters[k].add_to(feature_layers[k])

utils.add_map_infos(feature_layers, osm_hut_map, collapsed_legend=True)

In [ ]:
# explore number of huts for each provinces

hut_per_province = {k : len(osm_rifugi.loc[osm_rifugi.DEN_PROV == k]) for k in osm_rifugi.DEN_PROV.dropna().unique()}
for name, value in sorted(hut_per_province.items(), key=lambda item: item[1]):
  print(f'Number of Hut in {name}: {value}')

Number of Hut in Treviso: 4
Number of Hut in Verona: 19
Number of Hut in Vicenza: 29
Number of Hut in Belluno: 103
Number of Hut in Bolzano: 117
Number of Hut in Trento: 136


## &nbsp; 1.1 Alpine huts according to the elevation
First explorations to understand where are the highest huts.

In [ ]:
osm_hut_dolomities_map_ele = utils.get_new_map(title='Hut colored according to the elevation', tiles=tiles)

altitudes = [500, 1000, 1500, 2000, 2500, 2800]
colors = ['gray', 'lightgreen', 'green', 'orange', 'darkred','black']

feature_layers = {
    group:FeatureGroup(name=f"<span style='color:{colors[idx]}'>Hut higher than {group}m</span>") 
    for idx, group in enumerate(altitudes)
  }

feature_layers['dolomiti_area'] =  FeatureGroup(name='Area Dolomiti')
dolomiti_geo.add_to(feature_layers['dolomiti_area'])

# huts according to the elevation
for idx, row in osm_rifugi.iterrows():
  if row.ele != 0:
    color, marker_group = styles.hut_style_ele(row.ele)
    marker = Marker(
      location = [i[0] for i in reversed(row.geometry.xy)],
      popup = utils.get_info_from_row(row), 
      tooltip = utils.get_info_from_row(row),
      icon = Icon(color = color)
    )
    marker.add_to(feature_layers[marker_group])

utils.add_map_infos(feature_layers, osm_hut_dolomities_map_ele, collapsed_legend=True)

# &nbsp; 2. Alpine huts in Dolomities

Select only the huts that are nearby the dolomites

In [ ]:
buffered_dolomiti = dolomiti_df.copy()

# buffering on fly on epsg 32632
buffered_dolomiti.geometry = dolomiti_df.to_crs(epsg=32632).geometry.buffer(500).to_crs(epsg=4326).values
hut_in_dolomities_buffer = osm_rifugi.geometry.apply(lambda x: utils.element_within_area(x, buffered_dolomiti, 'name'))
assert buffered_dolomiti.crs == osm_rifugi.crs

# selecting only the huts that are closeby the dolomities
osm_rifugi['dolomities'] = hut_in_dolomities_buffer
osm_dolomites = osm_rifugi.loc[~osm_rifugi.dolomities.isna()].reset_index(drop=True)

In [ ]:
print(f'Number of hut in the dolomities: {len(osm_dolomites)}, total hut: {len(osm_rifugi)}')
osm_hut_dolomities_map = utils.get_new_map(title='Hut divided by Dolomities group', tiles=tiles)
unique_dolomities_group = osm_dolomites.dolomities.unique().tolist()

feature_layers = {group:FeatureGroup(name=f"Group of dolomities: {group}") for group in unique_dolomities_group}
feature_layers['dolomiti_area'] =  FeatureGroup(name='Area Dolomiti')
dolomiti_geo.add_to(feature_layers['dolomiti_area'])

# hut in the dolomities
for idx, row in osm_dolomites.iterrows():
  marker_group = row.dolomities
  marker = Marker(
      location = [i[0] for i in reversed(row.geometry.xy)],
      popup = utils.get_info_from_row(row), 
      tooltip = utils.get_info_from_row(row),
      icon = Icon(color=styles.c_colors[unique_dolomities_group.index(row.dolomities)])
  )
  marker.add_to(feature_layers[marker_group])

utils.add_map_infos(feature_layers, osm_hut_dolomities_map, collapsed_legend=True)

Number of hut in the dolomities: 91, total hut: 408


In [ ]:
# exploring the huts for each group of dolomities
hut_per_dolomities = {k : len(osm_dolomites.loc[osm_dolomites.dolomities == k]) for k in osm_dolomites.dolomities.unique()}
for name, value in sorted(hut_per_dolomities.items(), key=lambda item: item[1]):
  print(f'Number of Hut in {name}: {value}')

Number of Hut in Sistema 6 - Puez-Odle: 2
Number of Hut in Sistema 2 - Marmolada: 2
Number of Hut in Sistema 1 - Pelmo & Croda da Lago: 5
Number of Hut in Sistema 9 - Dolomiti di Brenta: 9
Number of Hut in Sistema 7 - Sciliar-Catinaccio & Latemar: 18
Number of Hut in Sistema 3 - Pale di San Martino: 19
Number of Hut in Sistema 5 - Dolomiti settentrionali: 36


## &nbsp; 2.1 Alpine huts elevation

In [ ]:
osm_hut_dolomities_map_ele = utils.get_new_map(title='Hut colored according to the elevation', tiles=tiles)

altitudes = [500, 1000, 1500, 2000, 2500, 2800]
colors = ['gray', 'lightgreen', 'green', 'orange', 'darkred','black']

feature_layers = {
    group:FeatureGroup(name=f"<span style='color:{colors[idx]}'>Hut higher than {group}m</span>") 
    for idx, group in enumerate(altitudes)
  }

feature_layers['dolomiti_area'] =  FeatureGroup(name='Area Dolomiti')
dolomiti_geo.add_to(feature_layers['dolomiti_area'])

# hut in dolomities according to the elevation
for idx, row in osm_dolomites.iterrows():
  color, marker_group = styles.hut_style_ele(row.ele)
  marker = Marker(
      location = [i[0] for i in reversed(row.geometry.xy)],
      popup = utils.get_info_from_row(row), 
      tooltip = utils.get_info_from_row(row),
      icon=folium.Icon(color = color)
  )
  
  marker.add_to(feature_layers[marker_group])

utils.add_map_infos(feature_layers, osm_hut_dolomities_map_ele, collapsed_legend=True)

## &nbsp; 2.1 SAT huts prices

In [102]:
# prices manually collected from the SAT information on prices
huts_prices = pd.read_csv('data/huts_prices.csv', encoding='latin-1',  on_bad_lines='skip', header=[0], sep=";")
sat_rifugi = gpd.read_file("data/alpine_huts/rifugi.shp") 
huts_prices.head(2)

name  elevation categoria  \
0          Rifugio Graffer al Grostè       2261         c   
1  Rifugio Guido Larcher al Cevedale       2607         d   

   posto_riposo_emergenze  posto_letto_soci  posto_letto_non_soci  \
0                     5.0                16                    32   
1                     5.0                17                    34   

   mezza_pensione_soci  mezza_pensione_non_soci acqua  
0                   48                       58   NaN  
1                   48                       58   NaN

In [103]:
idxs = []

# create common columns to merge the datasets
for _, row in huts_prices.iterrows():
  for idx, sat in sat_rifugi.iterrows():
    if row["name"] in sat.display_na:
      idxs.append(idx)

huts_prices.index = idxs
huts_prices_merged = huts_prices.merge(sat_rifugi, left_index=True, right_index=True).reset_index(drop=True)
huts_prices_merged = gpd.GeoDataFrame(huts_prices_merged)
huts_prices_merged = huts_prices_merged.to_crs(epsg=4326)

In [113]:
# summarinzing the prices information
cost_indicator_field = ["posto_riposo_emergenze",	"posto_letto_soci",	"posto_letto_non_soci",	"mezza_pensione_soci",	"mezza_pensione_non_soci"]
cost_indicator = []

for _, row in huts_prices.iterrows():
  cost_indicator.append(
      (row[cost_indicator_field].sum())
  )

huts_prices_merged['cost_indicator'] = cost_indicator

In [114]:
huts_prices_merged
osm_hut_dolomities_map_ele = utils.get_new_map(title='Hut colored according to the elevation with prices information', tiles=tiles)


altitudes = [500, 1000, 1500, 2000, 2500, 2800]
colors = ['gray', 'lightgreen', 'green', 'orange', 'darkred','black']

feature_layers = {
    group:FeatureGroup(name=f"<span style='color:{colors[idx]}'>Hut higher than {group}m</span>") 
    for idx, group in enumerate(altitudes)
  }

feature_layers['dolomiti_area'] =  FeatureGroup(name='Area Dolomiti')
dolomiti_geo.add_to(feature_layers['dolomiti_area'])

# hut in dolomities according to the elevation
for idx, row in huts_prices_merged.loc[:, ['name', 'elevation', 'categoria', 'extended_n', 'geometry', 'cost_indicator'] + cost_indicator_field].iterrows():
  color, marker_group = styles.hut_style_ele(row.elevation)
  marker = Marker(
      location = [i[0] for i in reversed(row.geometry.xy)],
      popup = utils.get_info_from_row(row), 
      tooltip = utils.get_info_from_row(row),
      icon=folium.Icon(color = color)
  )
  
  marker.add_to(feature_layers[marker_group])

utils.add_map_infos(feature_layers, osm_hut_dolomities_map_ele, collapsed_legend=True)

# OverPASS API for Peaks

query:
```
[out:json][timeout:25];
{{geocodeArea:Trento}}->.searchArea;
(
  // query part for: “peak”
  node["natural"="peak"](area.searchArea);
);
out body;
>;
out skel qt;
```

Doing this for Trento, Veneto, Bolzano.
Since they are many we directly filter them according to their prossimity to the dolomities.

In [ ]:
osm_peak = pd.concat([
  gpd.read_file('data/peaks/osm_peak_bolzano.geojson'),
  gpd.read_file('data/peaks/osm_peak_trento.geojson'),
  gpd.read_file('data/peaks/osm_peak_veneto.geojson'),                      
  gpd.read_file('data/peaks/osm_peak_friuli.geojson')                        
])

osm_peak.drop(columns=['id', '@id'], inplace=True)
osm_peak.replace({np.nan: None}, inplace=True)
osm_peak.dropna(subset=['ele'], inplace=True)
osm_peak.ele = osm_peak.ele.astype(float)
osm_peak.head(2)

alt_name alt_name:de alt_name:it alt_name:lld alt_name:vi alt_name_2  \
0     None        None        None         None        None       None   
1     None        None        None         None        None       None   

  artist_name comment description direction  ...  name:es name:sl name:slo  \
0        None    None        None      None  ...     None    None     None   
1        None    None        None      None  ...     None    None     None   

  notes old_name:it old_name:sl old_source:name population short_name:fur  \
0  None        None        None            None       None           None   
1  None        None        None            None       None           None   

  summit:bell  
0        None  
1        None  

[2 rows x 102 columns]

In [ ]:
#check peaks in dolomities
assert osm_peak.crs == buffered_dolomiti.crs
peak_in_dolomities_buffer = osm_peak.geometry.apply(lambda x: utils.element_within_area(x, buffered_dolomiti, 'name'))

osm_peak['dolomities'] = peak_in_dolomities_buffer
osm_dolomites_peak = osm_peak.loc[~osm_peak.dolomities.isna()].reset_index(drop=True)

In [ ]:
osm_peak_dolomities_map = utils.get_new_map(title='Peak colored according to the elevation', tiles=tiles)

altitudes = [500, 1000, 1500, 2000, 2500, 2800]
colors = ['gray', 'lightgreen', 'green', 'orange', 'darkred','black']

feature_layers = {
    group: FeatureGroup(name=f"<span style='color:{colors[idx]}'>Hut higher than {group}m</span>") 
    for idx, group in enumerate(altitudes)
  }

marker_clusters = {
    group: MarkerCluster(name=f"<span style='color:{colors[idx]}'>Hut higher than {group}m</span>") 
    for idx, group in enumerate(altitudes)
  }

feature_layers['dolomiti_area'] =  FeatureGroup(name='Area Dolomiti')
dolomiti_geo.add_to(feature_layers['dolomiti_area'])

# all peaks according to the elevation
for idx, row in osm_dolomites_peak.iterrows():
  color, marker_group = styles.hut_style_ele(row.ele)
  marker = Marker(
      location = [i[0] for i in reversed(row.geometry.xy)],
      popup = utils.get_info_from_row(row), 
      tooltip = utils.get_info_from_row(row),
      icon=folium.Icon(color=color)
  )

  marker.add_to(marker_clusters[marker_group])

for k,v in marker_clusters.items():
  marker_clusters[k].add_to(feature_layers[k])

utils.add_map_infos(feature_layers, osm_peak_dolomities_map, collapsed_legend=True)

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
peak_per_dolomities = {k : len(osm_dolomites_peak.loc[osm_dolomites_peak.dolomities == k]) for k in osm_dolomites_peak.dolomities.unique()}
for name, value in sorted(peak_per_dolomities.items(), key=lambda item: item[1]):
  print(f'Number of peaks in {name}: {value}')

Number of peaks in Sistema 8 - Bletterbach: 1
Number of peaks in Sistema 2 - Marmolada: 27
Number of peaks in Sistema 1 - Pelmo & Croda da Lago: 38
Number of peaks in Sistema 6 - Puez-Odle: 72
Number of peaks in Sistema 7 - Sciliar-Catinaccio & Latemar: 104
Number of peaks in Sistema 9 - Dolomiti di Brenta: 113
Number of peaks in Sistema 4 - Dolomiti friulane e d'Oltre Piave: 262
Number of peaks in Sistema 3 - Pale di San Martino: 271
Number of peaks in Sistema 5 - Dolomiti settentrionali: 342


In [ ]:
# very high peaks
osm_peak_dolomities_map = utils.get_new_map(title='Very high peak > 3000', tiles=tiles)

altitudes = [3000, 3100, 3200, 3300]
colors = ['orange', 'red', 'darkred','black']

feature_layers = {
    group:FeatureGroup(name=f"<span style='color:{colors[idx]}'>Hut higher than {group}m</span>") 
    for idx, group in enumerate(altitudes)
  }

feature_layers['dolomiti_area'] =  FeatureGroup(name='Area Dolomiti')
dolomiti_geo.add_to(feature_layers['dolomiti_area'])

for idx, row in osm_dolomites_peak.iterrows():
  if row.ele > 3000:
    color, marker_group = styles.hut_style_ele_high_peak(row.ele)
    marker = Marker(
        location = [i[0] for i in reversed(row.geometry.xy)],
      popup = utils.get_info_from_row(row), 
      tooltip = utils.get_info_from_row(row),
        icon=folium.Icon(color=color)
    )
    
    marker.add_to(feature_layers[marker_group])

utils.add_map_infos(feature_layers, osm_peak_dolomities_map, collapsed_legend=True)

Let's try to understand the Hut that are very close to some peaks

In [ ]:
# https://github.com/napo/geospatial_course_unitn/blob/master/code/solutions/02_exercise_spatial_relationship_and_operations.ipynb
from shapely.ops import nearest_points

def get_closest_point(peak, hut_unary, hut_dataset):
  _, hut = nearest_points(peak, hut_unary)
  return hut_dataset.loc[hut_dataset.geometry == hut].name.values[0]

hut_unary = osm_dolomites.geometry.unary_union
assert osm_dolomites_peak.crs == osm_dolomites.crs

osm_dolomites_high_peak = osm_dolomites_peak.copy()
osm_dolomites_high_peak = osm_dolomites_high_peak.loc[osm_dolomites_high_peak.ele > 3000]
osm_dolomites_high_peak['closest_hut'] = osm_dolomites_high_peak.geometry.apply(lambda x: get_closest_point(x, hut_unary, osm_dolomites))

In [ ]:
osm_peak_hut_dolomities_map = utils.get_new_map(title='Hut close to the highest Peaks', tiles=tiles)

groups = ['peak', 'hut']
colors = ['darkred', 'blue']

feature_layers = {
    group:FeatureGroup(name=f"<span style='color:{colors[idx]}'>{group.capitalize()}</span>") 
    for idx, group in enumerate(groups)
  }

feature_layers['dolomiti_area'] =  FeatureGroup(name='Area Dolomiti')
dolomiti_geo.add_to(feature_layers['dolomiti_area'])

# high peak
for idx, row in osm_dolomites_high_peak.iterrows():
  marker = Marker(
      location = [i[0] for i in reversed(row.geometry.xy)],
      popup = utils.get_info_from_row(row), 
      tooltip = utils.get_info_from_row(row),
      icon=folium.Icon(color='darkred')
  )

  marker.add_to(feature_layers['peak'])

# hut closesest to the highest peaks
set_uniques = osm_dolomites_high_peak['closest_hut'].unique()
for idx, row in osm_dolomites.loc[osm_dolomites.name.isin(set_uniques)].iterrows():
  marker = Marker(
      location = [i[0] for i in reversed(row.geometry.xy)],
      popup = utils.get_info_from_row(row), 
      tooltip = utils.get_info_from_row(row),
      icon=folium.Icon(color='blue')
  )
  marker.add_to(feature_layers['hut'])

utils.add_map_infos(feature_layers, osm_peak_hut_dolomities_map, collapsed_legend=True)

# explore absolute distances

In [ ]:
res = []
osm_dolomites_32632 = osm_dolomites.to_crs(epsg=32632)
osm_dolomites_high_peak.reset_index(inplace=True, drop=True)

assert osm_dolomites_32632.crs == osm_dolomites_high_peak.to_crs(epsg=32632).crs
for idx, row in osm_dolomites_high_peak.to_crs(epsg=32632).iterrows():
  peak = row["geometry"]
  hut = osm_dolomites_32632.loc[osm_dolomites_32632['name'] == row["closest_hut"]].geometry.values[0]
  res.append({'distance' : round(peak.distance(hut))})

assert osm_dolomites_high_peak.crs == osm_dolomites.crs
for idx, row in osm_dolomites_high_peak.iterrows():
  peak = row["geometry"]
  hut = osm_dolomites.loc[osm_dolomites['name'] == row["closest_hut"]].geometry.values[0]
  res[idx]['geometry'] = LineString([peak,hut])
      
linestring_distance = gpd.GeoDataFrame(res, crs="EPSG:4326") 

In [ ]:
osm_peak_hut_dolomities_map = utils.get_new_map(title='Shortest Path between peaks and huts', tiles=tiles)
groups = ['peak', 'hut', 'peak_hut_path']
colors = ['darkred', 'blue', 'black']

feature_layers = {
    group:FeatureGroup(name=f"<span style='color:{colors[idx]}'>{group.capitalize()}</span>") 
    for idx, group in enumerate(groups)
  }

feature_layers['dolomiti_area'] =  FeatureGroup(name='Area Dolomiti')
dolomiti_geo.add_to(feature_layers['dolomiti_area'])

# peaks
for idx, row in osm_dolomites_high_peak.iterrows():
  marker = Marker(
    location = [i[0] for i in reversed(row.geometry.xy)],
    popup = utils.get_info_from_row(row), 
    tooltip = utils.get_info_from_row(row),
    icon=folium.Icon(color='darkred')
  )
  marker.add_to(feature_layers['peak'])


# huts close to the peaks
set_uniques = osm_dolomites_high_peak['closest_hut'].unique()
for idx, row in osm_dolomites.loc[osm_dolomites.name.isin(set_uniques)].iterrows():
  marker = Marker(
    location = [i[0] for i in reversed(row.geometry.xy)],
    popup = utils.get_info_from_row(row), 
    tooltip = utils.get_info_from_row(row),
    icon=folium.Icon(color='blue')
  )
  marker.add_to(feature_layers['hut'])


# Linestring huts-peaks
for idx, row in linestring_distance.iterrows():
  info = f'distance {row.distance}'
  line = PolyLine(
    locations = [list(reversed(i)) for i in list(row.geometry.coords)],
    popup = info, 
    tooltip = info,
    color='black',
    weight=10,
  )

  line.add_to(feature_layers['peak_hut_path'])

feature_layers['dolomiti_area'].add_to(osm_peak_hut_dolomities_map)
utils.add_map_infos(feature_layers, osm_peak_hut_dolomities_map, collapsed_legend=True)